In [1]:
import pandas as pd
import numpy as np
import copy
import holoviews as hv
import plotly.figure_factory as ff
import time
import matplotlib.pyplot as plt
from collections import Counter
import plotly.graph_objects as go

In [7]:
fips = pd.read_csv('./fips-codes/county_fips_master.csv', encoding='latin-1')
fips_n = fips.to_numpy()
CA_fips = fips_n[fips_n[:,2] == 'CA'][:,:2]
CA_fip_dict = {fc[1].rsplit(' ',1)[0]:fc[0] for fc in CA_fips}

In [8]:
processed_data = pd.read_csv('processed_data.csv',\
                             usecols = ['ID','Start_Time','Weather_Condition','Start_Lat','Start_Lng','County']).to_numpy()
processed_data

array([['A-1', '05:46:00', 'Rain', 39.865147, -84.058723, 'Montgomery'],
       ['A-2', '06:07:59', 'Rain', 39.928059, -82.831184, 'Franklin'],
       ['A-3', '06:49:27', 'Fog', 39.063148, -84.032608, 'Clermont'],
       ...,
       ['A-4239404', '19:00:21', 'Cloudy', 33.77545, -117.84779,
        'Orange'],
       ['A-4239405', '19:00:21', 'Clear', 33.99246, -118.40302,
        'Los Angeles'],
       ['A-4239406', '18:52:06', 'Clear', 34.13393, -117.23092,
        'San Bernardino']], dtype=object)

In [9]:
data_rain = processed_data[processed_data[:,2] == 'Rain']
data_clear = processed_data[processed_data[:,2] == 'Clear']
data_fog = processed_data[processed_data[:,2] == 'Fog']
data_snow = processed_data[processed_data[:,2] == 'Snow']
data_cloudy = processed_data[processed_data[:,2] == 'Cloudy']
data_dust = processed_data[processed_data[:,2] == 'Dust']

In [10]:
rain_fips = [CA_fip_dict[county] for county in data_rain[:,5] if county in CA_fip_dict]
clear_fips = [CA_fip_dict[county] for county in data_clear[:,5] if county in CA_fip_dict]
fog_fips = [CA_fip_dict[county] for county in data_fog[:,5] if county in CA_fip_dict]
snow_fips = [CA_fip_dict[county] for county in data_snow[:,5] if county in CA_fip_dict]
cloudy_fips = [CA_fip_dict[county] for county in data_cloudy[:,5] if county in CA_fip_dict]
dust_fips = [CA_fip_dict[county] for county in data_dust[:,5] if county in CA_fip_dict]
#-----------------------
rain_fip_hist = Counter(rain_fips)
clear_fip_hist = Counter(clear_fips)
fog_fip_hist = Counter(fog_fips)
snow_fip_hist = Counter(snow_fips)
cloudy_fip_hist = Counter(cloudy_fips)
dust_fip_hist = Counter(dust_fips)
fip_hist = [rain_fip_hist,clear_fip_hist,fog_fip_hist,snow_fip_hist,cloudy_fip_hist,dust_fip_hist]
#-----------------------
rain_fip_vals, rain_values = list(rain_fip_hist.keys()),list(rain_fip_hist.values())
clear_fip_vals, clear_values = list(clear_fip_hist.keys()),list(clear_fip_hist.values())
fog_fip_vals, fog_values = list(fog_fip_hist.keys()),list(fog_fip_hist.values())
snow_fip_vals, snow_values = list(snow_fip_hist.keys()),list(snow_fip_hist.values())
cloudy_fip_vals, cloudy_values = list(cloudy_fip_hist.keys()),list(cloudy_fip_hist.values())
dust_fip_vals, dust_values = list(dust_fip_hist.keys()),list(dust_fip_hist.values())

In [11]:
keyList = list(CA_fips[:,0])
CA_dict = {key: [0,0,0,0,0,0] for key in keyList}
for num, dictionary in enumerate(fip_hist):
    for key in dictionary:
        CA_dict[key][num] = dictionary[key]
# list(CA_dict.values())
CA_dict_df = pd.DataFrame.from_dict(CA_dict, orient='index', columns = ['Rain', 'Clear','Fog','Snow','Cloudy','Dust'])
CA_dict_df['FIP'] = ['0'+str(fip) for fip in CA_dict_df.index]
CA_dict_df.index = range(len(CA_dict_df))

In [12]:
CA_dict_df

Rain   Clear    Fog  Snow  Cloudy  Dust    FIP
0    3597   27974   7443     0   21710     0  06001
1       4      69      3    38      34     0  06003
2       2     789    106     0     302     0  06005
3     108    1577    182     2     780     0  06007
4       0     962    115     0     272     0  06009
5      53     502     52     0     129     0  06011
6    2235   20486   3106     0    6154     0  06013
7      71     179    112     0     178     0  06015
8      35    2999    482   131    1104     0  06017
9     587    5613   2143     0    5699     7  06019
10     11     338     46     0     265     0  06021
11    173     955    251     7     846     0  06023
12      1      71      3     0      22     0  06025
13      6     278     17     2      96     0  06027
14    597   10455   1722    38    2463    19  06029
15    741    5770   1886    67    3115     1  06031
16   1842   13606   4810  1311    8636     0  06033
17     30     415     25    39     200     0  06035
18  12695  193862  35269    61   63581    56  06037
19    140    2180    528     0     733     0  06039
20    353    4167   1125     0    2109     0  06041
21      9     415     72     0      87     0  06043
22    204    1780    135     1     637     0  06045
23    123    3391    691     0     859     2  06047
24      6      65      7    24      79     0  06049
25     13     463     30    61      92     0  06051
26    403    4960   1387     0    2405     0  06053
27    303    2395    661     0    1084     0  06055
28    126    1775    418   247     605     0  06057
29   6515   47865   9291   123   45786     3  06059
30    228    5534    846   246    1702     0  06061
31     21     302     29    14     155     0  06063
32   1994   34210   3567     0    9581    15  06065
33   2794   35042   4220     0   11389     5  06067
34     16    1134    165     0     295     0  06069
35   3258   27027   8289    44   18372    81  06071
36   3817   25357   6763    30   21399    14  06073
37    685    2993   1135     0    6327     0  06075
38    869   12879   1815     0    2661     1  06077
39    206    2874    428     0     977     1  06079
40   1267    6437   2251     0    9749     0  06081
41    384    3599    827     1    1678     1  06083
42   2429   16290   4828     0   18836     0  06085
43    483    3655   1143     0    2041     0  06087
44    153    1462    242     7     495     0  06089
45     12      79     21    27      41     0  06091
46     45     593     59    50     301     0  06093
47    810    9073   1337     2    2459     0  06095
48    899    6881   2803     0    3521     0  06097
49    305    6377    956     0    1490     0  06099
50     40     823     78     6     202     0  06101
51     80     865     89     1     263     0  06103
52      4     232     30     0     113     0  06105
53    300    3910    757     0     854     0  06107
54      0    1053     96     0     248     0  06109
55    646    7006   1309     0    2250     4  06111
56    160    4033    317     0     836     0  06113
57     81    1290    155     4     339     0  06115

In [13]:
# fips = [CA_fip_dict[county] for county in processed_data[:,5] if county in CA_fip_dict]
# fip_hist = Counter(fips)
# fip_vals, values = list(fip_hist.keys()),list(fip_hist.values())
# prob_values = list(np.array(values)/sum(values))

In [14]:
fig = ff.create_choropleth(fips=rain_fip_vals, values=rain_values, scope = ['CA'])
fig.show()

In [42]:
df = pd.read_csv("https://raw.githubusercontent.com/plotly/datasets/master/fips-unemp-16.csv",
                   dtype={"fips": str})

In [46]:
type(df.iloc[1]['fips'])

str

In [15]:
str_rain_fip_vals = ['0'+str(fip) for fip in rain_fip_vals]
np.array([str_rain_fip_vals,rain_values]).T

array([['06095', '810'],
       ['06067', '2794'],
       ['06001', '3597'],
       ['06085', '2429'],
       ['06113', '160'],
       ['06013', '2235'],
       ['06075', '685'],
       ['06081', '1267'],
       ['06097', '899'],
       ['06099', '305'],
       ['06007', '108'],
       ['06041', '353'],
       ['06033', '1842'],
       ['06045', '204'],
       ['06087', '483'],
       ['06055', '303'],
       ['06077', '869'],
       ['06017', '35'],
       ['06061', '228'],
       ['06011', '53'],
       ['06047', '123'],
       ['06101', '40'],
       ['06053', '403'],
       ['06019', '587'],
       ['06069', '16'],
       ['06073', '3817'],
       ['06071', '3258'],
       ['06083', '384'],
       ['06037', '12695'],
       ['06111', '646'],
       ['06059', '6515'],
       ['06065', '1994'],
       ['06031', '741'],
       ['06005', '2'],
       ['06057', '126'],
       ['06115', '81'],
       ['06051', '13'],
       ['06079', '206'],
       ['06029', '597'],
       ['06103', '80'

In [17]:
CA_df = pd.DataFrame(np.array([str_rain_fip_vals,rain_values]).T,columns=['id','rain'])
CA_df

id   rain
0   06095    810
1   06067   2794
2   06001   3597
3   06085   2429
4   06113    160
5   06013   2235
6   06075    685
7   06081   1267
8   06097    899
9   06099    305
10  06007    108
11  06041    353
12  06033   1842
13  06045    204
14  06087    483
15  06055    303
16  06077    869
17  06017     35
18  06061    228
19  06011     53
20  06047    123
21  06101     40
22  06053    403
23  06019    587
24  06069     16
25  06073   3817
26  06071   3258
27  06083    384
28  06037  12695
29  06111    646
30  06059   6515
31  06065   1994
32  06031    741
33  06005      2
34  06057    126
35  06115     81
36  06051     13
37  06079    206
38  06029    597
39  06103     80
40  06089    153
41  06021     11
42  06023    173
43  06107    300
44  06015     71
45  06043      9
46  06039    140
47  06063     21
48  06093     45
49  06035     30
50  06091     12
51  06025      1
52  06027      6
53  06105      4
54  06049      6
55  06003      4

In [2]:
from urllib.request import urlopen
import json
with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    counties = json.load(response)

In [3]:
counties

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'GEO_ID': '0500000US01001',
    'STATE': '01',
    'COUNTY': '001',
    'NAME': 'Autauga',
    'LSAD': 'County',
    'CENSUSAREA': 594.436},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-86.496774, 32.344437],
      [-86.717897, 32.402814],
      [-86.814912, 32.340803],
      [-86.890581, 32.502974],
      [-86.917595, 32.664169],
      [-86.71339, 32.661732],
      [-86.714219, 32.705694],
      [-86.413116, 32.707386],
      [-86.411172, 32.409937],
      [-86.496774, 32.344437]]]},
   'id': '01001'},
  {'type': 'Feature',
   'properties': {'GEO_ID': '0500000US01009',
    'STATE': '01',
    'COUNTY': '009',
    'NAME': 'Blount',
    'LSAD': 'County',
    'CENSUSAREA': 644.776},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-86.577799, 33.765316],
      [-86.759144, 33.840617],
      [-86.953664, 33.815297],
      [-86.954305, 33.844862],
      [-86.96296, 33.844865],
      [-86.9

In [4]:
CA_counties = {'type':'FeatureCollection','features':[]}
for info in counties['features']:
    if info['properties']['STATE'] == '06':
        CA_counties['features'].append(info)

In [5]:
CA_counties

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'GEO_ID': '0500000US06005',
    'STATE': '06',
    'COUNTY': '005',
    'NAME': 'Amador',
    'LSAD': 'County',
    'CENSUSAREA': 594.583},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-120.995497, 38.225405],
      [-121.027084, 38.300252],
      [-121.027507, 38.508292],
      [-120.813554, 38.562193],
      [-120.627604, 38.503143],
      [-120.510596, 38.511467],
      [-120.301721, 38.549109],
      [-120.098322, 38.709029],
      [-120.072392, 38.702767],
      [-120.072484, 38.509869],
      [-120.380707, 38.461042],
      [-120.423215, 38.473322],
      [-120.893792, 38.221277],
      [-120.995497, 38.225405]]]},
   'id': '06005'},
  {'type': 'Feature',
   'properties': {'GEO_ID': '0500000US06021',
    'STATE': '06',
    'COUNTY': '021',
    'NAME': 'Glenn',
    'LSAD': 'County',
    'CENSUSAREA': 1313.947},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-122.937654, 39.79815

In [18]:
CA_fip_dict

{'Alameda': 6001,
 'Alpine': 6003,
 'Amador': 6005,
 'Butte': 6007,
 'Calaveras': 6009,
 'Colusa': 6011,
 'Contra Costa': 6013,
 'Del Norte': 6015,
 'El Dorado': 6017,
 'Fresno': 6019,
 'Glenn': 6021,
 'Humboldt': 6023,
 'Imperial': 6025,
 'Inyo': 6027,
 'Kern': 6029,
 'Kings': 6031,
 'Lake': 6033,
 'Lassen': 6035,
 'Los Angeles': 6037,
 'Madera': 6039,
 'Marin': 6041,
 'Mariposa': 6043,
 'Mendocino': 6045,
 'Merced': 6047,
 'Modoc': 6049,
 'Mono': 6051,
 'Monterey': 6053,
 'Napa': 6055,
 'Nevada': 6057,
 'Orange': 6059,
 'Placer': 6061,
 'Plumas': 6063,
 'Riverside': 6065,
 'Sacramento': 6067,
 'San Benito': 6069,
 'San Bernardino': 6071,
 'San Diego': 6073,
 'San Francisco': 6075,
 'San Joaquin': 6077,
 'San Luis Obispo': 6079,
 'San Mateo': 6081,
 'Santa Barbara': 6083,
 'Santa Clara': 6085,
 'Santa Cruz': 6087,
 'Shasta': 6089,
 'Sierra': 6091,
 'Siskiyou': 6093,
 'Solano': 6095,
 'Sonoma': 6097,
 'Stanislaus': 6099,
 'Sutter': 6101,
 'Tehama': 6103,
 'Trinity': 6105,
 'Tulare': 61

In [19]:
counties.keys()

dict_keys(['type', 'features'])

In [20]:
import plotly.express as px
#import plotly.graph_objects as px

#df = px.data.election()
#geojson = px.data.election_geojson()

traces = []
buttons = []
cols_dd = np.array(['Rain', 'Clear','Fog','Snow','Cloudy','Dust'])

for weather in cols_dd:
    traces.append(px.choropleth(CA_dict_df, geojson=CA_counties, color=weather,
                    locations="FIP", featureidkey="id",
                    projection="mercator"
                    ).data[0]
                 )
    buttons.append(dict(label=weather,
                        method="update",
                        args=[{"visible":weather == cols_dd},
                              {"title":weather}]))
    
# fig2 = px.choropleth(CA_dict_df, geojson=CA_counties, color="Dust",
#                     locations="FIP", featureidkey="id",
#                     projection="mercator"
#                     )
# fig.add_trace(fig2.data[0])

# fig.update_geos(fitbounds="locations", visible=False)
# fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

# buttons.append(dict(label='Snow',
#                         method="update",
#                         args=[{"visible":[True,False]},
#                               {"title":'Rain'}]))
    
# buttons.append(dict(label='Dust',
#                         method="update",
#                         args=[{"visible":[False,True]},
#                               {"title":'Dust'}]))

updatemenus = [{"active":0,
                "buttons":buttons,
               }]

# Show figure
fig = go.Figure(data=traces,
                 layout=dict(updatemenus=updatemenus))
#fig.update_layout(updatemenus=updatemenus)
# This is in order to get the first title displayed correctly

fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

first_title = cols_dd[0]
fig.update_layout(title=f"<b>{first_title}</b>",title_x=0.5)

fig.show()

In [197]:
cols_dd = np.array(['Rain', 'Clear','Fog','Snow','Cloudy','Dust'])
'Rain' == cols_dd

array([ True, False, False, False, False, False])

In [183]:
type(fig.data)

tuple

In [156]:
CA_dict_df

Rain   Clear    Fog  Snow  Cloudy  Dust    FIP
0    3597   27974   7443     0   21710     0  06001
1       4      69      3    38      34     0  06003
2       2     789    106     0     302     0  06005
3     108    1577    182     2     780     0  06007
4       0     962    115     0     272     0  06009
5      53     502     52     0     129     0  06011
6    2235   20486   3106     0    6154     0  06013
7      71     179    112     0     178     0  06015
8      35    2999    482   131    1104     0  06017
9     587    5613   2143     0    5699     7  06019
10     11     338     46     0     265     0  06021
11    173     955    251     7     846     0  06023
12      1      71      3     0      22     0  06025
13      6     278     17     2      96     0  06027
14    597   10455   1722    38    2463    19  06029
15    741    5770   1886    67    3115     1  06031
16   1842   13606   4810  1311    8636     0  06033
17     30     415     25    39     200     0  06035
18  12695  193862  35269    61   63581    56  06037
19    140    2180    528     0     733     0  06039
20    353    4167   1125     0    2109     0  06041
21      9     415     72     0      87     0  06043
22    204    1780    135     1     637     0  06045
23    123    3391    691     0     859     2  06047
24      6      65      7    24      79     0  06049
25     13     463     30    61      92     0  06051
26    403    4960   1387     0    2405     0  06053
27    303    2395    661     0    1084     0  06055
28    126    1775    418   247     605     0  06057
29   6515   47865   9291   123   45786     3  06059
30    228    5534    846   246    1702     0  06061
31     21     302     29    14     155     0  06063
32   1994   34210   3567     0    9581    15  06065
33   2794   35042   4220     0   11389     5  06067
34     16    1134    165     0     295     0  06069
35   3258   27027   8289    44   18372    81  06071
36   3817   25357   6763    30   21399    14  06073
37    685    2993   1135     0    6327     0  06075
38    869   12879   1815     0    2661     1  06077
39    206    2874    428     0     977     1  06079
40   1267    6437   2251     0    9749     0  06081
41    384    3599    827     1    1678     1  06083
42   2429   16290   4828     0   18836     0  06085
43    483    3655   1143     0    2041     0  06087
44    153    1462    242     7     495     0  06089
45     12      79     21    27      41     0  06091
46     45     593     59    50     301     0  06093
47    810    9073   1337     2    2459     0  06095
48    899    6881   2803     0    3521     0  06097
49    305    6377    956     0    1490     0  06099
50     40     823     78     6     202     0  06101
51     80     865     89     1     263     0  06103
52      4     232     30     0     113     0  06105
53    300    3910    757     0     854     0  06107
54      0    1053     96     0     248     0  06109
55    646    7006   1309     0    2250     4  06111
56    160    4033    317     0     836     0  06113
57     81    1290    155     4     339     0  06115

In [149]:
fig.data[0]

Choropleth({
    'colorscale': [[0.0, '#636efa'], [1.0, '#636efa']],
    'featureidkey': 'id',
    'geo': 'geo',
    'geojson': {'features': [{'geometry': {'coordinates': [[[-120.995497,
                                                           38.225405],
                                                           [-121.027084,
                                                           38.300252],
                                                           [-121.027507,
                                                           38.508292],
                                                           [-120.813554,
                                                           38.562193],
                                                           [-120.627604,
                                                           38.503143],
                                                           [-120.510596,
                                                           38.511467],
                      

In [139]:
df = pd.read_csv("https://raw.githubusercontent.com/plotly/datasets/master/volcano.csv")
df

V1   V2   V3   V4   V5   V6   V7   V8   V9  V10  ...  V52  V53  V54  V55  \
0   100  100  101  101  101  101  101  100  100  100  ...  107  107  107  106   
1   101  101  102  102  102  102  102  101  101  101  ...  108  108  107  107   
2   102  102  103  103  103  103  103  102  102  102  ...  109  108  108  107   
3   103  103  104  104  104  104  104  103  103  103  ...  109  109  108  108   
4   104  104  105  105  105  105  105  104  104  103  ...  110  109  109  108   
..  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
82   99   99   99   99  100  100  101  101  102  102  ...   95   95   95   95   
83   98   99   99   99   99  100  100  101  101  102  ...   95   95   94   94   
84   98   98   98   99   99   99  100  100  101  101  ...   94   94   94   94   
85   97   98   98   98   99   99   99  100  100  100  ...   94   94   94   94   
86   97   97   97   98   98   99   99   99  100  100  ...   94   94   94   94   

    V56  V57  V58  V59  V60  V61  
0   106  105  105  104  104  103  
1   106  106  105  105  104  104  
2   107  106  106  105  105  104  
3   107  107  106  106  105  105  
4   107  107  107  106  106  105  
..  ...  ...  ...  ...  ...  ...  
82   94   94   94   94   94   94  
83   94   94   94   94   94   94  
84   94   94   94   94   94   94  
85   94   94   94   94   94   94  
86   94   94   94   94   94   94  

[87 rows x 61 columns]

In [137]:
type(fig)

plotly.graph_objs._figure.Figure

In [136]:
import plotly.graph_objects as go

import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/2011_us_ag_exports.csv')

fig = go.Figure(data=go.Choropleth(
    locations=CA_df['id'], # Spatial coordinates
    z = CA_df['rain'].astype(float), # Data to be color-coded
    locationmode = 'geojson-id', # set of locations match entries in `locations`
    colorscale = 'Reds',
    colorbar_title = "Millions USD",
))

fig.update_layout(
    title_text = '2011 US Agriculture Exports by State',
    geo_scope='usa', # limite map scope to USA
)

fig.show()

In [133]:
df

code           state category  total exports   beef    pork  poultry  \
0    AL         Alabama    state        1390.63   34.4    10.6    481.0   
1    AK          Alaska    state          13.31    0.2     0.1      0.0   
2    AZ         Arizona    state        1463.17   71.3    17.9      0.0   
3    AR        Arkansas    state        3586.02   53.2    29.4    562.9   
4    CA      California    state       16472.88  228.7    11.1    225.4   
5    CO        Colorado    state        1851.33  261.4    66.0     14.0   
6    CT     Connecticut    state         259.62    1.1     0.1      6.9   
7    DE        Delaware    state         282.19    0.4     0.6    114.7   
8    FL         Florida    state        3764.09   42.6     0.9     56.9   
9    GA         Georgia    state        2860.84   31.0    18.9    630.4   
10   HI          Hawaii    state         401.84    4.0     0.7      1.3   
11   ID           Idaho    state        2078.89  119.8     0.0      2.4   
12   IL        Illinois    state        8709.48   53.7   394.0     14.0   
13   IN         Indiana    state        5050.23   21.9   341.9    165.6   
14   IA            Iowa    state       11273.76  289.8  1895.6    155.6   
15   KS          Kansas    state        4589.01  659.3   179.4      6.4   
16   KY        Kentucky    state        1889.15   54.8    34.2    151.3   
17   LA       Louisiana    state        1914.23   19.8     0.8     77.2   
18   ME           Maine    state         278.37    1.4     0.5     10.4   
19   MD        Maryland    state         692.75    5.6     3.1    127.0   
20   MA   Massachusetts    state         248.65    0.6     0.5      0.6   
21   MI        Michigan    state        3164.16   37.7   118.1     32.6   
22   MN       Minnesota    state        7192.33  112.3   740.4    189.2   
23   MS     Mississippi    state        2170.80   12.8    30.4    370.8   
24   MO        Missouri    state        3933.42  137.2   277.3    196.1   
25   MT         Montana    state        1718.00  105.0    16.7      1.7   
26   NE        Nebraska    state        7114.13  762.2   262.5     31.4   
27   NV          Nevada    state         139.89   21.8     0.2      0.0   
28   NH   New Hampshire    state          73.06    0.6     0.2      0.8   
29   NJ      New Jersey    state         500.40    0.8     0.4      4.6   
30   NM      New Mexico    state         751.58  117.2     0.1      0.3   
31   NY        New York    state        1488.90   22.2     5.8     17.7   
32   NC  North Carolina    state        3806.05   24.8   702.8    598.4   
33   ND    North Dakota    state        3761.96   78.5    16.1      0.5   
34   OH            Ohio    state        3979.79   36.2   199.1    129.9   
35   OK        Oklahoma    state        1646.41  337.6   265.3    131.1   
36   OR          Oregon    state        1794.57   58.8     1.4     14.2   
37   PA    Pennsylvania    state        1969.87   50.9    91.3    169.8   
38   RI    Rhode Island    state          31.59    0.1     0.1      0.2   
39   SC  South Carolina    state         929.93   15.2    10.9    186.5   
40   SD    South Dakota    state        3770.19  193.5   160.2     29.3   
41   TN       Tennessee    state        1535.13   51.1    17.6     82.4   
42   TX           Texas    state        6648.22  961.0    42.7    339.2   
43   UT            Utah    state         453.39   27.9    59.0     23.1   
44   VT         Vermont    state         180.14    6.2     0.2      0.9   
45   VA        Virginia    state        1146.48   39.5    16.9    164.7   
46   WA      Washington    state        3894.81   59.2     0.0     35.6   
47   WV   West Virginia    state         138.89   12.0     0.3     45.4   
48   WI       Wisconsin    state        3090.23  107.3    38.6     34.5   
49   WY         Wyoming    state         349.69   75.1    33.2      0.1   

     dairy  fruits fresh  fruits proc  total fruits  veggies fresh  \
0     4.06           8.0         17.1         25.11            5.5   
1     0.19           0.0          0.0

In [50]:
geojson

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[-73.6363215300962, 45.5759177646435],
       [-73.6362833815582, 45.5758266113331],
       [-73.6446417578686, 45.5658132919643],
       [-73.6453511352974, 45.5647725775888],
       [-73.648867564748, 45.5586898267402],
       [-73.6513170845065, 45.5545659435652],
       [-73.6515658357324, 45.5554439857955],
       [-73.6660837831645, 45.5596724837829],
       [-73.6706609041685, 45.5610978251999],
       [-73.6676019919116, 45.5632340862888],
       [-73.6645385824068, 45.5642716484367],
       [-73.663663123697, 45.5654269638586],
       [-73.663336397858, 45.5666288247853],
       [-73.6637764768649, 45.5678900619231],
       [-73.6625073244826, 45.5688479494114],
       [-73.6624620526633, 45.5708304456346],
       [-73.6620201425015, 45.5713925326191],
       [-73.6616100197742, 45.5737924780218],
       [-73.6612199500215, 45.5747171555678],
       [-7

In [52]:
df

district  Coderre  Bergeron  \
0                                  101-Bois-de-Liesse     2481      1829   
1                               102-Cap-Saint-Jacques     2525      1163   
2                                11-Sault-au-Récollet     3348      2770   
3                                        111-Mile-End     1734      4782   
4                                      112-DeLorimier     1770      5933   
5                                    113-Jeanne-Mance     1455      3599   
6                                    12-Saint-Sulpice     3252      2521   
7                          121-La Pointe-aux-Prairies     5456      1760   
8                             122-Pointe-aux-Trembles     4734      1879   
9                            123-Rivière-des-Prairies     5737       958   
10                                        13-Ahuntsic     2979      3430   
11                                  131-Saint-Édouard     1827      6408   
12                             132-Étienne-Desmarteau     2331      5748   
13                                 133-Vieux-Rosemont     2670      4962   
14                                 134-Marie-Victorin     3673      3155   
15                           14-Bordeaux-Cartierville     3612      1554   
16                                 141-Côte-de-Liesse     4308      1320   
17                                 142-Norman-McLaren     4104      1459   
18                              151-Saint-Léonard-Est     3931       882   
19                            152-Saint-Léonard-Ouest     5387      1184   
20  161-Saint-HenriPetite-BourgognePointe-Saint-Ch...     2432      3368   
21                                162-Saint-PaulÉmard     2566      2092   
22                      171-ChamplainL'Île-des-Soeurs     3347      2562   
23                           172-Desmarchais-Crawford     2476      2631   
24                                   181-Peter-McGill     1451       754   
25                                  182-Saint-Jacques     1906      2169   
26                                   183-Sainte-Marie     1347      2827   
27                                   191-Saint-Michel     3668       984   
28                              192-François-Perrault     2878      2666   
29                                       193-Villeray     2201      5819   
30                                 194-Parc-Extension     2420      1793   
31                                           21-Ouest     2184       691   
32                                             22-Est     1589       708   
33                                          23-Centre     2526       851   
34                                      31-Darlington     1873      1182   
35                                 32-Côte-des-Neiges     1644      1950   
36                                         33-Snowdon     1548      1503   
37                             34-Notre-Dame-de-Grâce     1773      2653   
38                                          35-Loyola     2040      1437   
39                                        41-du Canal     1165       832   
40                                42-J.-Émery-Provost     1193       653   
41                                    43-Fort-Rolland     1325      1205   
42                               51-Sault-Saint-Louis     4201      1642   
43                                 52-Cecil-P.-Newman     3536      1330   
44                                 61-Pierre-Foretier      631       258   
45                            62-Denis-Benjamin-Viger      595       226   
46                                  63-Jacques-Bizard      518       224   
47                                64-Sainte-Geneviève      332       131   
48                                  71-Tétreaultville     3694      2589   
49                        72-MaisonneuveLongue-Pointe     2746      3250   
50                                       73-Hochelaga     1546      3679   
51                                      74-Louis-Riel     3509      2178   
52               

In [124]:
import plotly.graph_objects as px
import numpy as np
  
# creating random data through randomint
# function of numpy.random
np.random.seed(42)
  
random_x = np.random.randint(1, 101, 100)
random_y = np.random.randint(1, 101, 100)
  
plot = px.Figure(data=[px.Scatter(
    x=random_x,
    y=random_y,
    mode='markers',)
])
  
# Add dropdown
# plot.update_layout(
#     updatemenus=[
#         dict(
#             buttons=list([
#                 dict(
#                     args=["type", "scatter"],
#                     label="Scatter Plot",
#                     method="restyle"
#                 ),
#                 dict(
#                     args=["type", "bar"],
#                     label="Bar Chart",
#                     method="restyle"
#                 )
#             ]),
#             direction="down",
#         ),
#     ]
# )
  
plot.show()

In [20]:
import dash
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output
import plotly.express as px

df = px.data.iris()
all_dims = ['sepal_length', 'sepal_width', 
            'petal_length', 'petal_width']

app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id="dropdown",
        options=[{"label": x, "value": x} 
                 for x in all_dims],
        value=all_dims[:2],
        multi=True
    ),
    dcc.Graph(id="splom"),
])

@app.callback(
    Output("splom", "figure"), 
    [Input("dropdown", "value")])
def update_bar_chart(dims):
    fig = px.scatter_matrix(
        df, dimensions=dims, color="species")
    return fig

app.run_server(debug=True)

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: on


SystemExit: 1

C:\Users\panda\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3445: UserWarning:

To exit: use 'exit', 'quit', or Ctrl-D.



In [171]:
# Data
df = px.data.gapminder().query("year==2007")
df = df.rename(columns=dict(pop="Population",
                            gdpPercap="GDP per Capita",
                            lifeExp="Life Expectancy"))
cols_dd = ["Population", "GDP per Capita", "Life Expectancy"]
# we need to add this to select which trace 
# is going to be visible
visible = np.array(cols_dd)

# define traces and buttons at once
traces = []
buttons = []
for value in cols_dd:
    traces.append(go.Choropleth(
       locations=df['iso_alpha'], # Spatial coordinates
        z=df[value].astype(float), # Data to be color-coded
        colorbar_title=value,
        visible= True if value==cols_dd[0] else False))

    buttons.append(dict(label=value,
                        method="update",
                        args=[{"visible":list(visible==value)},
                              {"title":f"<b>{value}</b>"}]))

# fig = px.choropleth(CA_df, geojson=CA_counties, color="rain",
#                     locations="id", featureidkey="id",
#                     projection="mercator"
#                     )
# fig.update_geos(fitbounds="locations", visible=False)
# fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

# traces.append(ff.create_choropleth(fips=rain_fip_vals, values=rain_values, scope = ['CA']))
# traces.append(ff.create_choropleth(fips=dust_fip_vals, values=dust_values, scope = ['CA']))

# buttons.append(dict(label='rain',
#                         method="update",
#                         args=[{"visible":list(visible==value)},
#                               {"title":f"<b>{value}</b>"}]))
    
# buttons.append(dict(label='dust',
#                         method="update",
#                         args=[{"visible":list(visible==value)},
#                               {"title":f"<b>{value}</b>"}]))

updatemenus = [{"active":0,
                "buttons":buttons,
               }]


# print(type(go.Choropleth(
#        locations=df['iso_alpha'], # Spatial coordinates
#         z=df[value].astype(float), # Data to be color-coded
#         colorbar_title=value,
#         visible= True if value==cols_dd[0] else False)))
    
# Show figure
fig = go.Figure(data=traces,
                layout=dict(updatemenus=updatemenus))
# This is in order to get the first title displayed correctly
first_title = cols_dd[0]
fig.update_layout(title=f"<b>{first_title}</b>",title_x=0.5)
fig.show()

In [3]:
df

country continent  year  Life Expectancy  Population  \
11           Afghanistan      Asia  2007           43.828    31889923   
23               Albania    Europe  2007           76.423     3600523   
35               Algeria    Africa  2007           72.301    33333216   
47                Angola    Africa  2007           42.731    12420476   
59             Argentina  Americas  2007           75.320    40301927   
...                  ...       ...   ...              ...         ...   
1655             Vietnam      Asia  2007           74.249    85262356   
1667  West Bank and Gaza      Asia  2007           73.422     4018332   
1679         Yemen, Rep.      Asia  2007           62.698    22211743   
1691              Zambia    Africa  2007           42.384    11746035   
1703            Zimbabwe    Africa  2007           43.487    12311143   

      GDP per Capita iso_alpha  iso_num  
11        974.580338       AFG        4  
23       5937.029526       ALB        8  
35       6223.367465       DZA       12  
47       4797.231267       AGO       24  
59      12779.379640       ARG       32  
...              ...       ...      ...  
1655     2441.576404       VNM      704  
1667     3025.349798       PSE      275  
1679     2280.769906       YEM      887  
1691     1271.211593       ZMB      894  
1703      469.709298       ZWE      716  

[142 rows x 8 columns]

In [14]:
import plotly.graph_objects as go

import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/2011_us_ag_exports.csv')

fig = go.Figure(data=go.Choropleth(
    locations=df['code'], # Spatial coordinates
    z = df['total exports'].astype(float), # Data to be color-coded
    locationmode = 'geojson-id', # set of locations match entries in `locations`
    colorscale = 'Reds',
    colorbar_title = "Millions USD",
))

fig.update_layout(
    title_text = '2011 US Agriculture Exports by State',
    geo_scope='usa', # limite map scope to USA
)

fig.show()

In [12]:
from urllib.request import urlopen
import json
with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    counties = json.load(response)

import pandas as pd
df = pd.read_csv("https://raw.githubusercontent.com/plotly/datasets/master/fips-unemp-16.csv",
                   dtype={"fips": str})

import plotly.express as px

fig = px.choropleth(df, geojson=counties, locations='fips', color='unemp',
                           color_continuous_scale="Viridis",
                           range_color=(0, 12),
                           scope="CA",
                           labels={'unemp':'unemployment rate'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

ValueError: 
    Invalid value of type 'builtins.str' received for the 'scope' property of layout.geo
        Received value: 'CA'

    The 'scope' property is an enumeration that may be specified as:
      - One of the following enumeration values:
            ['world', 'usa', 'europe', 'asia', 'africa', 'north
            america', 'south america']

In [141]:
import plotly
from plotly.graph_objs import Scattergl, Layout
import plotly.figure_factory as ff
import plotly.graph_objs as go
import pandas as pd

plotly.offline.init_notebook_mode(connected=True)

columns = ["x","y","z"]
x = [1,2,3,4,5,6,7,8,9,10]
y = [2,3,4,5,6,7,8,9,10,11]
z = [3,4,5,6,7,8,9,10,11,12]

colors = ['#ffaeb9', '#ffb6c0', '#ffbec7', '#ffc6ce', '#ffced5',
          '#ffd6dc', '#ffdee3', '#ffe6ea', '#ffeef1', '#fff6f8']
color_buttons = []
column_buttons_x = []
column_buttons_y = []

for i in colors:
    color_buttons.append(
        dict(args=['line.color', i],
             label=i, method='restyle')
    )
for j in columns:
    column_buttons_x.append(
        dict(args=['x',j],
            label=j,method='update')
    )
for k in columns:
    column_buttons_y.append(
        dict(args=['y',k],
            label=k,method='update')
    )
    
layout = Layout(

    annotations=[dict(text='Change Color',
                      x=-0.25, y=0.83,
                      xref='paper', yref='paper',
                      showarrow=False)],
    updatemenus=list([
        dict(x=-0.1, y=0.7,
             yanchor='middle',
             bgcolor='#c7c7c7',
             buttons=list(color_buttons)),
        dict(x=-0.1,y=0.5,
            yanchor = 'middle',
            bgcolor = '#c7c7c7',
            buttons=list(column_buttons_x)),
        dict(x=-0.1,y=0.3,
            yanchor = 'middle',
            bgcolor = '#c7c7c7',
            buttons=list(column_buttons_y))
    ])
)

trace = go.Scatter( x=[j],
                    y=[k],
                    mode='markers'
                            )

data = [trace]
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [ ]:
df